# 1. Datensatz

## 1.1 Infos zum Datensatz

Ein erheblicher Teil des Gesamtenergieverbrauchs weltweit entfällt heutzutage auf Gebäude, insbesondere auf Heizung, Lüftung und Klimatechnik. Hier bieten sich durch intelligente Steuerung große Einsparpotenziale. Ein Baustein dafür sind Sensoren, die erkennen, ob sich Menschen in bestimmten Teilen des Gebäudes aufhalten und diese Information an die Gebäudesteuerung weiterleiten, sodass Energieverbraucher dynamisch zu- und abgeschaltet werden können. Der vorliegende Datensatz (Datensatz-Sensor.csv) enthält Messdaten, die von einem Sensor in einem Bürogebäude aufgezeichnet wurden. Eine Zeile beschreibt die Erfassung verschiedener Messwerte zu einem bestimmten Zeitpunkt an einem festen Ort (d.h., der Sensor wurde nicht bewegt). Leider kann der Sensor aktuell noch nicht messen, ob sich Personen im Raum befinden. Für den vorliegenden Zeitraum wurde die Anwesenheit einer Person aber manuell kontrolliert und den Messdaten hinzugefügt. Insgesamt existieren folgende Felder in den Daten:
- Datum: Zeitstempel im Format JJJJ-MM-DD hh:mm:ss
- Temperatur: Temperatur in Grad Celsius (°C)
- Luftfeuchtigkeit: relative Luftfeuchtigkeit in %
- CO2: CO2 Gehalt in ppm
- Wassergehalt: Verhältnis von Gewicht des verdunsteten Wassers zum Gewicht der trockenen Luft in kg Wasserdampf / kg Luft (abgeleitet aus Temperatur und Luftfeuchtigkeit)
- Anwesenheit: Ist eine Person anwesend (1) oder nicht (0).

# 2. Explorative Datenanalyse (EDA)

## 2.1 Überblick

Bevor wir mit der Bereinigung oder Modellierung beginnen, verschaffen wir uns einen Überblick über die Struktur der Rohdaten.
Ziel dieser ersten Inspektion ist es:
1.  Die **Dimensionen** des Datensatzes zu prüfen (Wie viele Zeilen/Spalten?).
2.  Die **Datentypen** zu validieren (Wird das Datum korrekt erkannt?).
3.  Erste **Auffälligkeiten** zu identifizieren (Gibt es fehlende Werte oder offensichtliche Ausreißer in der Statistik?).

Dafür brauchen wir folgende Imports:

In [1]:
import pandas as pd
import numpy as np
import plotly.express as px

In diesem Schritt laden wir den Datensatz `Datensatz-Sensor.csv` und prüfen die Datenqualität.  
Wir untersuchen die Struktur mit `df.info()` und schauen uns statistische Kennzahlen mit `df.describe()` an, um erste Auffälligkeiten (z.B. fehlende Werte oder unrealistische Ausreißer) zu identifizieren.

In [2]:
df = pd.read_csv('data/Datensatz-Sensor.csv')

# Die ersten 5 Zeilen anzeigen (Wie sehen die Daten aus?)
display(df.head())

# Infos zu Datentypen und fehlenden Werten
print("--- Info zu Datentypen ---")
print(df.info())

# Statistische Übersicht
print("\n--- Statistische Beschreibung ---")
display(df.describe())

Datum  Temperatur  Feuchtigkeit         CO2  Wassergehalt  \
0  2015-02-02 14:19:00     23.7000        26.272  749.200000      0.004764   
1  2015-02-02 14:19:59     23.7180        26.290  760.400000      0.004773   
2  2015-02-02 14:21:00     23.7300        26.230  769.666667      0.004765   
3  2015-02-02 14:22:00     23.7225        26.125  774.750000      0.004744   
4  2015-02-02 14:23:00     23.7540        26.200  779.000000      0.004767   

   Anwesenheit  
0            1  
1            1  
2            1  
3            1  
4            1

--- Info zu Datentypen ---
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 19236 entries, 0 to 19235
Data columns (total 6 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   Datum         19236 non-null  object 
 1   Temperatur    19134 non-null  float64
 2   Feuchtigkeit  18915 non-null  float64
 3   CO2           19236 non-null  float64
 4   Wassergehalt  18777 non-null  float64
 5   Anwesenheit   19236 non-null  int64  
dtypes: float64(4), int64(1), object(1)
memory usage: 901.8+ KB
None

--- Statistische Beschreibung ---


Temperatur  Feuchtigkeit           CO2  Wassergehalt   Anwesenheit
count  19134.000000  18915.000000  19236.000000  18777.000000  19236.000000
mean      21.322743     27.451396    634.818354      0.004189      0.226606
std        3.908221      5.008853    260.246196      0.000759      0.418647
min       19.000000     16.745000      0.000000      0.002674      0.000000
25%       20.133333     24.290000    454.500000      0.003699      0.000000
50%       20.675000     27.171429    545.500000      0.004278      0.000000
75%       21.600000     31.050000    734.541667      0.004799      0.000000
max       55.998944     39.500000   2028.500000      0.006476      1.000000

## 2.2 Auffälligkeiten in den Daten:
Bei der Betrachtung der Statistik (`describe`) und Datentypen (`info`) fallen folgende Probleme auf, die im nächsten Schritt bereinigt werden müssen:

1.  **Falsches Datumsformat:** Die Spalte `Datum` wird aktuell als Text (`object`) erkannt und nicht als Zeitstempel. Zudem sind die Sekunden oft auf `:59`, was auf einen leichten Zeitversatz hindeutet.
2.  **Unrealistische Temperaturen:** Der Maximalwert liegt bei über 50°C. Da es sich um ein Büro handelt, ist dies ein offensichtlicher Messfehler (Ausreißer).
3.  **CO2-Ausfälle:** Der Minimalwert bei CO2 ist 0.0 ppm. Da die natürliche Außenluft bereits ca. 400 ppm CO2 enthält, deutet dies auf Sensorausfälle hin.

## 2.3 Visualisierung der Rohdaten
Um die Verteilung und mögliche Fehler besser zu erkennen, plotten wir die Zeitreihen für Temperatur und CO2.
Hierbei erwarten wir, die oben identifizierten Ausreißer (Temperatur > 50°C und CO2 = 0) grafisch bestätigen zu können.

In [3]:
# Damit Plotly die Zeitachse richtig malt, wandeln wir das Datum kurz um
df['Datum'] = pd.to_datetime(df['Datum'])

# Plot: Temperatur
fig_temp = px.scatter(df, x='Datum', y='Temperatur', title='Temperaturverlauf')
fig_temp.update_xaxes(tickmode = "linear")
fig_temp.show()

# Plot: CO2
fig_co2 = px.scatter(df, x='Datum', y='CO2', title='CO2-Verlauf')
fig_co2.update_xaxes(tickmode = "linear")
fig_co2.show()

# Ein Boxplot
fig_box_co2 = px.box(df, y='CO2', title='Statistische Verteilung & Ausreißer (co2)')
fig_box_co2.show()

fig_box_temp = px.box(df, y='Temperatur', title='Statistische Verteilung & Ausreißer (Temperatur)')
fig_box_temp.show()

# Plot: Anwesenheit am Wochentag
df["Anwesenheit_Prozent"] = df.groupby(df["Datum"].dt.date)["Anwesenheit"].transform(lambda x: x.sum() / x.count() * 100)

grouped_percentages = df.groupby(df["Datum"].dt.dayofweek).agg(Anwesenheit_Prozent=("Anwesenheit_Prozent", "first")).reset_index()

fig_anwesenheit = px.bar(
    grouped_percentages,
    x="Datum",
    y="Anwesenheit_Prozent",
    title="Prozentuale Anwesenheit pro Tag",
)
fig_anwesenheit.update_xaxes(tickmode="linear")

## 2.4 Analyse fehlender Werte
Datenlücken können durch Sensorausfälle oder Übertragungsfehler entstehen. Da wir nicht mit fehlenden Werte (`NaN`) arbeiten wollen, prüfen wir hier, welche Spalten betroffen sind.
Dies liefert uns die Begründung für die spätere **Interpolation** der Werte.

In [4]:
# Berechnen der fehlenden Werte pro Spalte
missing_count = df.isnull().sum()

# Wir filtern und zeigen nur Spalten an, die wirklich fehlende Werte haben
missing_data = missing_count[missing_count > 0]

print("Anzahl fehlender Werte pro Spalte:")
print(missing_data)

Anzahl fehlender Werte pro Spalte:
Temperatur      102
Feuchtigkeit    321
Wassergehalt    459
dtype: int64


## 2.5 Korrelationsanalyse
In diesem Schritt untersuchen wir die statistischen Zusammenhänge zwischen den verschiedenen Messwerten.

**Ziele:**
1.  **Relevanz prüfen:** Welche Sensoren korrelieren stark mit der Zielvariable `Anwesenheit`? Ein hoher Wert (nahe 1 oder -1) bedeutet, dass der Sensor ein guter Prädiktor ist.
2.  **Redundanz erkennen:** Korrelieren zwei Sensoren (z.B. Feuchtigkeit und Wassergehalt) extrem stark miteinander (> 0.9), enthalten sie fast die gleiche Information. Eine der beiden Spalten kann später entfernt werden, um das Modell nicht zu verwirren (Multikollinearität).

In [5]:
# Korrelationsmatrix berechnen
numeric_df = df.select_dtypes(include=['number'])
corr_matrix = numeric_df.corr()

# Heatmap anzeigen
fig_corr = px.imshow(corr_matrix, text_auto='.2f', aspect="auto", color_continuous_scale='RdBu_r', title="Korrelationsmatrix")
fig_corr.show()

# Anwesenheit vs. CO2
# Da Anwesenheit (0/1) kategorisch ist, eignet sich ein Boxplot besser als ein Scatterplot
df['Status'] = df['Anwesenheit'].map({0: 'Leer', 1: 'Besetzt'})

fig_box = px.box(df, x='Status', y='CO2', color='Status',title='Einfluss von Anwesenheit auf den CO2-Gehalt', color_discrete_map={'Leer': 'blue', 'Besetzt': 'red'})
fig_box.show()

# Aufräumen
df = df.drop(columns=['Status'])

# 3. Datenvorverarbeitung und Feature Engineering

## 3.1 Datenvorverarbeitung
Im ersten Schritt korrigieren wir technische Unsauberkeiten in den Rohdaten.
* **Zeit-Korrektur:** Sekunden werden auf die nächste volle Minute gerundet (z.B. `xx:xx:59` $\rightarrow$ `xx:(xx+1):00`), um saubere Zeitstempel zu erhalten.
* **Ausreißer entfernen:** Wir setzen physikalisch unmögliche Werte (Temperatur > 40°C, CO2 < 50 ppm) auf `NaN`.
* **Interpolation:** Die entstandenen Lücken füllen wir linear auf, um den Zeitreihen-Charakter zu erhalten.

In [6]:
# Wir arbeiten absofort auf einer Kopie weiter
df_clean = df.copy()

### Zeit-Korrektur

In [7]:
# Datum korrigieren
if df_clean['Datum'].dtype == 'object':
    df_clean['Datum'] = pd.to_datetime(df_clean['Datum'])

# Runden: Wenn Sekunde == 59, addiere 1 Sekunde
mask_59 = df_clean['Datum'].dt.second == 59
if mask_59.sum() > 0:
    df_clean.loc[mask_59, 'Datum'] += pd.Timedelta(seconds=1)

### Ausreißer entfernen

In [8]:
# Ausreißer entfernen (auf NaN setzen)
if 'Temperatur' in df_clean.columns:
    df_clean.loc[df_clean['Temperatur'] > 40, 'Temperatur'] = np.nan

if 'CO2' in df_clean.columns:
    df_clean.loc[df_clean['CO2'] < 50, 'CO2'] = np.nan

### Interpolation

In [9]:
# Interpolation (Lücken füllen)
# Wir wählen nur numerische Spalten (ausgenommen Anwesenheit, Datum)
cols_to_interpolate = ['Temperatur', 'Feuchtigkeit', 'CO2', 'Wassergehalt']

for col in cols_to_interpolate:
    if col in df_clean.columns:
        df_clean[col] = df_clean[col].interpolate(method='linear').bfill().ffill()

# Check
print("Daten nach Bereinigung:")
display(df_clean.head())

Daten nach Bereinigung:


Datum  Temperatur  Feuchtigkeit         CO2  Wassergehalt  \
0 2015-02-02 14:19:00     23.7000        26.272  749.200000      0.004764   
1 2015-02-02 14:20:00     23.7180        26.290  760.400000      0.004773   
2 2015-02-02 14:21:00     23.7300        26.230  769.666667      0.004765   
3 2015-02-02 14:22:00     23.7225        26.125  774.750000      0.004744   
4 2015-02-02 14:23:00     23.7540        26.200  779.000000      0.004767   

   Anwesenheit  Anwesenheit_Prozent  
0            1            34.939759  
1            1            34.939759  
2            1            34.939759  
3            1            34.939759  
4            1            34.939759

### Visualisierung der neuen Daten

In [10]:
# Plot: Temperatur
fig_temp = px.scatter(df_clean, x='Datum', y='Temperatur', title='Temperaturverlauf')
fig_temp.update_xaxes(tickmode = "linear")
fig_temp.show()

# Plot: CO2
fig_co2 = px.scatter(df_clean, x='Datum', y='CO2', title='CO2-Verlauf')
fig_co2.update_xaxes(tickmode = "linear")
fig_co2.show()

# Optional: Ein Boxplot zeigt Ausreißer noch brutaler
fig_box_co2 = px.box(df_clean, y='CO2', title='Statistische Verteilung & Ausreißer (co2)')
fig_box_co2.show()

fig_box_temp = px.box(df_clean, y='Temperatur', title='Statistische Verteilung & Ausreißer (Temperatur)')
fig_box_temp.show()

## 3.2 Feature Engineering  
Zeit ist für ein Modell schwer zu verstehen. 23:00 Uhr und 00:00 Uhr liegen zahlenmäßig weit auseinander, in der Realität aber direkt nebeneinander.
* **Zyklische Transformation:** Wir berechnen die "Minute des Tages" und transformieren diese mit Sinus und Cosinus. So liegen Abend und Morgen im Vektorraum nah beieinander.
* **Logische Features:** Wir definieren `Ist_Buerozeit` (Mo-Fr, 07:00–18:00 Uhr), da hier die Wahrscheinlichkeit für Anwesenheit am höchsten ist. Außerdem schauen wir, ob es sich um einen Feiertag handelt und definierten `Tagesart_Werktag`

In [11]:
import holidays

# Wir arbeiten mit dem bereinigten DataFrame weiter
df_features = df_clean.copy()

# Hilfsgrößen berechnen
stunde = df_features['Datum'].dt.hour
minute = df_features['Datum'].dt.minute
wochentag = df_features['Datum'].dt.dayofweek # 0=Montag, 6=Sonntag
df_features['Jahr'] = df_features['Datum'].dt.year

# Zyklische Zeit-Features (Sinus/Cosinus)
# Minute des Tages (0 bis 1439)
minute_of_day = stunde * 60 + minute

# Transformation (2*pi*t / T)
df_features['time_sin'] = np.sin(2 * np.pi * minute_of_day / 1440)
df_features['time_cos'] = np.cos(2 * np.pi * minute_of_day / 1440)

# Delta berechnen (Veränderung der letzten 15 Minuten)
# periods=15 setzt voraus, dass 1 Zeile = 1 Minute ist
df_features['CO2_Delta_15min'] = df_features['CO2'].diff(periods=15)

# Die ersten 15 Zeilen werden NaN sein -> mit 0 füllen
df_features['CO2_Delta_15min'] = df_features['CO2_Delta_15min'].fillna(0)

df_features['Wochentag'] = wochentag




# Logische Features
# Bürozeit: Zwischen 07:00 und 18:00 Uhr UND Wochentag ist Montag-Freitag (<= 4)
#df_features['Ist_Buerozeit'] = ((stunde >= 7) & (stunde <= 18) & (wochentag <= 4)).astype(int)


de_holidays = holidays.DE(years=df_features['Jahr'].unique()) 

def bestimme_tagesart_werktag(datum):
    # Prüfen auf Feiertag
    if datum in de_holidays:
        return False
    # Wochenend Prüfung
    if datum.dayofweek >= 5:
        return False
    return True

df_features['Tagesart_Werktag'] = df_features['Datum'].apply(bestimme_tagesart_werktag)

print('Neue Zeit-Features:')
#display(df_features[['Datum', 'time_sin', 'time_cos', 'Ist_Buerozeit', 'Tagesart_Werktag']].head(10))

Neue Zeit-Features:


In [12]:
fig_werktag = px.histogram(df_features, x=df_features.Datum, color="Tagesart_Werktag").update_xaxes(tickangle=-45, tickmode="linear")
fig_werktag.show()

## 3.3 Aufräumen
* **Feature Selection:** Abschließend entfernen wir das ursprüngliche `Datum` (da vom Modell nicht lesbar) sowie redundante Spalten.

In [13]:
# Aufräumen
# Wir entfernen Spalten, die wir nicht mehr brauchen
cols_to_drop = ['Datum', "Jahr", "Anwesenheit_Prozent"] 

df_final = df_features.drop(columns=[c for c in cols_to_drop if c in df_features.columns])

print("Finaler Datensatz für das Training:")
display(df_final.head())

Finaler Datensatz für das Training:


Temperatur  Feuchtigkeit         CO2  Wassergehalt  Anwesenheit  time_sin  \
0     23.7000        26.272  749.200000      0.004764            1 -0.569997   
1     23.7180        26.290  760.400000      0.004773            1 -0.573576   
2     23.7300        26.230  769.666667      0.004765            1 -0.577145   
3     23.7225        26.125  774.750000      0.004744            1 -0.580703   
4     23.7540        26.200  779.000000      0.004767            1 -0.584250   

   time_cos  CO2_Delta_15min  Wochentag  Tagesart_Werktag  
0 -0.821647              0.0          0              True  
1 -0.819152              0.0          0              True  
2 -0.816642              0.0          0              True  
3 -0.814116              0.0          0              True  
4 -0.811574              0.0          0              True

# 4. Modelle Modellierung und Evaluation

## 4.1 Vorbereitung: Split und Skalierung
Wir verwenden nun den bereinigten Datensatz `df_final`.
1.  **Vorbereitung:** Wir trennen die Zielvariable (`Anwesenheit`) von den Features (X).
2.  **Train-Test-Split:** Aufteilung in 80% Training und 20% Test.
3.  **Skalierung:** Standardisierung der Werte für die Logistische Regression.

In [14]:
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.linear_model import LogisticRegressionCV
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import RandomizedSearchCV
from sklearn.metrics import accuracy_score, classification_report
from sklearn.model_selection import TimeSeriesSplit
tscv = TimeSeriesSplit(n_splits=5)

# Daten vorbereiten
X = df_final.drop('Anwesenheit', axis=1)
y = df_final['Anwesenheit']

# Train-Test-Split (80% Training, 20% Test)
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, shuffle=False)

# Skalierung
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train) # Fit nur auf Training!
X_test_scaled = scaler.transform(X_test)       # Transform auf Test

# Liste für Ergebnisse vorbereiten
results_list = []

print(f"Fertig. Trainingsdaten: {X_train.shape}")

Fertig. Trainingsdaten: (15388, 9)


## 4.2 Modell 1: Logistische Regression
Wir starten mit der Logistischen Regression als Basis. Sie trennt die Klassen linear.

In [15]:
# Modell initialisieren & trainieren
model_lr = LogisticRegressionCV(cv=tscv, scoring="roc_auc", class_weight="balanced")
model_lr.fit(X_train_scaled, y_train)

# Vorhersage
y_pred_lr = model_lr.predict(X_test_scaled)

# Auswertung speichern
report_lr = classification_report(y_test, y_pred_lr, output_dict=True, zero_division=0)

results_list.append({
    "Modell": "Logistische Regression",
    "Accuracy": accuracy_score(y_test, y_pred_lr),
    "Precision (1)": report_lr.get('1', {}).get('precision', 0.0),
    "Recall (1)": report_lr.get('1', {}).get('recall', 0.0),
    "F1-Score (1)": report_lr.get('1', {}).get('f1-score', 0.0)
})

print("Logistische Regression abgeschlossen.")

Logistische Regression abgeschlossen.


## 4.4 Modell 2: Random Forest
Der Random Forest kombiniert viele Entscheidungsbäume ("Ensemble"). Er ist meist robuster und genauer als einzelne Bäume.

In [16]:
# Modell initialisieren & trainieren mit Parameter
model_rf = RandomForestClassifier()
model_rf.fit(X_train, y_train)

# Vorhersage
y_pred_rf = model_rf.predict(X_test)

# Auswertung speichern
report_rf = classification_report(y_test, y_pred_rf, output_dict=True)
results_list.append({
    "Modell": "Random Forest",
    "Accuracy": accuracy_score(y_test, y_pred_rf),
    "Precision (1)": report_rf['1']['precision'],
    "Recall (1)": report_rf['1']['recall'],
    "F1-Score (1)": report_rf['1']['f1-score']
})

print("Random Forest abgeschlossen.")

Random Forest abgeschlossen.


## 4.5 Modell 3: Gradient Boosing

In [17]:
from sklearn.ensemble import GradientBoostingClassifier

# Modell initialisieren
gb_model = GradientBoostingClassifier()

print("Trainiere Gradient Boosting...")
gb_model.fit(X_train, y_train)

# Vorhersage
y_pred_gb = gb_model.predict(X_test)

# Auswertung
report_gb = classification_report(y_test, y_pred_gb, output_dict=True)
results_list.append({
    "Modell": "Gradient Boosting",
    "Accuracy": accuracy_score(y_test, y_pred_gb),
    "Precision (1)": report_gb['1']['precision'],
    "Recall (1)": report_gb['1']['recall'],
    "F1-Score (1)": report_gb['1']['f1-score']
})


print("Gradient Boosting abgeschlossen.")

# Optional: Feature Importance beim Boosting ansehen
importances_gb = gb_model.feature_importances_
df_imp_gb = pd.DataFrame({'Feature': X.columns, 'Importance': importances_gb}).sort_values('Importance')
fig_gb = px.bar(df_imp_gb, x='Importance', y='Feature', orientation='h', title='Wichtigste Features (Gradient Boosting)')
fig_gb.show()

Trainiere Gradient Boosting...
Gradient Boosting abgeschlossen.


## 4.5 Modell 4 (Optional): Entscheidungsbaum (Decision Tree)
Der Decision Tree lernt komplexe, nicht-lineare Regeln. Er ist gut interpretierbar, neigt aber ohne Begrenzung zum Overfitting.

In [18]:
# Modell initialisieren & trainieren
model_dt = DecisionTreeClassifier()
model_dt.fit(X_train, y_train)

# Vorhersage
y_pred_dt = model_dt.predict(X_test)

# Auswertung speichern
report_dt = classification_report(y_test, y_pred_dt, output_dict=True)
results_list.append({
    "Modell": "Entscheidungsbaum (Optional)",
    "Accuracy": accuracy_score(y_test, y_pred_dt),
    "Precision (1)": report_dt['1']['precision'],
    "Recall (1)": report_dt['1']['recall'],
    "F1-Score (1)": report_dt['1']['f1-score']
})

print("Entscheidungsbaum abgeschlossen.")

Entscheidungsbaum abgeschlossen.


## 4.5 Ergebnisvergleich
Wir fassen die Metriken aller drei Modelle zusammen. Besonderes schauen wir auf den **F1-Score der Klasse 1 (Anwesend)**, da dieser Precision und Recall vereint und uns zeigt, wie gut das Modell Personen erkennt.

In [19]:
# DataFrame erstellen
results_df = pd.DataFrame(results_list)
results_df = results_df.round(4)

# Anzeigen
print("Vergleich der Modelle:")
display(results_df)

Vergleich der Modelle:


Modell  Accuracy  Precision (1)  Recall (1)  \
0        Logistische Regression    0.8870         0.6188      1.0000   
1                 Random Forest    0.9137         0.6855      0.9788   
2             Gradient Boosting    0.8485         0.5480      0.9943   
3  Entscheidungsbaum (Optional)    0.8313         0.5227      0.9306   

   F1-Score (1)  
0        0.7645  
1        0.8063  
2        0.7066  
3        0.6694

# 5. Modell-Optimierung (Hyperparameter Tuning)

## 5.1 GridSearch
Obwohl der Random Forest bereits sehr gute Ergebnisse liefert (siehe Vergleichstabelle), nutzen wir **GridSearch mit 5-facher Kreuzvalidierung**, um die optimalen Einstellungen zu finden und sicherzugehen, dass das Ergebnis kein Zufall war.
Wir testen verschiedene Kombinationen aus:
* `n_estimators`: Anzahl der Bäume (50, 100, 200)
* `max_depth`: Maximale Tiefe der Bäume (begrenzt vs. unbegrenzt)

In [20]:
from sklearn.model_selection import GridSearchCV

# 1. Wir definieren das Gitter (die Kandidaten)
param_grid = {
    'n_estimators': [50, 100, 200],
    'max_depth': [None, 3, 5, 10, 20],
    'min_samples_split': [2, 5, 10, 20],
    'min_samples_leaf': [1, 2, 4, 6],
}

# 2. GridSearch initialisieren
# cv=5 bedeutet: Wir testen jede Einstellung 5-mal auf unterschiedlichen Daten-Teilen
grid_search = GridSearchCV(estimator=RandomForestClassifier(),
                           param_grid=param_grid,
                           cv=tscv,
                           n_jobs=-1, # Alle Prozessorkerne nutzen
                           verbose=1)

print("Starte Optimierung...")
grid_search.fit(X_train, y_train)

# Das beste Modell speichern
best_rf_model = grid_search.best_estimator_

print(f"\nBeste Parameter: {grid_search.best_params_}")
print(f"Beste Accuracy (Cross-Validation): {grid_search.best_score_:.4f}")

from sklearn.metrics import classification_report, accuracy_score

# Vorhersage mit dem GEWINNER-Modell auf den TEST-Daten
y_pred_optimiert = best_rf_model.predict(X_test)
# Jetzt vergleichen wir fair:
print("--- Ergebnis des optimierten Modells auf Testdaten ---")
print(f"Echte Accuracy: {accuracy_score(y_test, y_pred_optimiert):.4f}")
print(classification_report(y_test, y_pred_optimiert))

Starte Optimierung...
Fitting 5 folds for each of 240 candidates, totalling 1200 fits

Beste Parameter: {'max_depth': 3, 'min_samples_leaf': 4, 'min_samples_split': 10, 'n_estimators': 200}
Beste Accuracy (Cross-Validation): 0.9261
--- Ergebnis des optimierten Modells auf Testdaten ---
Echte Accuracy: 0.9467
              precision    recall  f1-score   support

           0       1.00      0.94      0.97      3142
           1       0.78      1.00      0.87       706

    accuracy                           0.95      3848
   macro avg       0.89      0.97      0.92      3848
weighted avg       0.96      0.95      0.95      3848



## 5.2 Feature Importance
Ein großer Vorteil von Entscheidungsbäumen ist ihre Interpretierbarkeit. Wir extrahieren die **Feature Importance**, um zu verstehen, welche Sensoren für die Vorhersage der Anwesenheit am wichtigsten sind.
* **Erwartung:** CO2 und die zeitliche Veränderung (Delta) sollten einen großen Einfluss haben.

In [21]:
# Daten für den Plot holen
importances = best_rf_model.feature_importances_
feature_names = X.columns # Unsere Features

# DataFrame erstellen
df_imp = pd.DataFrame({
    'Feature': feature_names,
    'Importance': importances
}).sort_values(by='Importance', ascending=True)

# Plotten
fig_imp = px.bar(df_imp, 
                 x='Importance', 
                 y='Feature', 
                 orientation='h', 
                 title='Einflussfaktoren: Worauf achtet die KI?',
                 text_auto='.3f',
                 color='Importance',
                 color_continuous_scale='Viridis')

fig_imp.update_layout(showlegend=False)
fig_imp.show()

## 5.3 Fehleranalyse (Confusion Matrix)
Abschließend prüfen wir mit der Confusion Matrix, wo genau das optimierte Modell noch Fehler macht.

In [29]:
from sklearn.metrics import confusion_matrix

# Vorhersage mit dem BESTEN Modell
y_pred_opt = best_rf_model.predict(X_test)
y_probs_gb = gb_model.predict(X_test)
y_probs_lg = model_lr.predict(X_test_scaled)

# Matrix berechnen
cm = confusion_matrix(y_test, y_pred_opt)
gb = confusion_matrix(y_test, y_probs_gb)
lg = confusion_matrix(y_test, y_probs_lg)

# Plotten
fig_cm = px.imshow(cm,
                   text_auto=True,
                   x=['Leer (0)', 'Besetzt (1)'],
                   y=['Leer (0)', 'Besetzt (1)'],
                   color_continuous_scale='Blues',
                   title="Confusion Matrix (Optimiertes Modell)")

fig_cm.update_layout(xaxis_title="Vorhersage", yaxis_title="Wahrheit")
fig_cm.show()

fig_cm2 = px.imshow(gb,
                   text_auto=True,
                   x=['Leer (0)', 'Besetzt (1)'],
                   y=['Leer (0)', 'Besetzt (1)'],
                   color_continuous_scale='Blues',
                   title="Confusion Matrix (Gradient Boosting)")

fig_cm2.update_layout(xaxis_title="Vorhersage", yaxis_title="Wahrheit")
fig_cm2.show()

fig_cm3 = px.imshow(lg,
                   text_auto=True,
                   x=['Leer (0)', 'Besetzt (1)'],
                   y=['Leer (0)', 'Besetzt (1)'],
                   color_continuous_scale='Blues',
                   title="Confusion Matrix (Logistische Regression)")

fig_cm3.update_layout(xaxis_title="Vorhersage", yaxis_title="Wahrheit")
fig_cm3.show()


## 5.4 ROC-Kurve

In [23]:
from sklearn.metrics import roc_curve, auc
import plotly.graph_objects as go

# Wahrscheinlichkeiten für die Klasse 1 (Besetzt) holen
y_probs_rf = best_rf_model.predict_proba(X_test)[:, 1]
y_probs_gb = gb_model.predict_proba(X_test)[:, 1]
y_probs_lg = model_lr.predict_proba(X_test_scaled)[:, 1]

# ROC Daten berechnen
fpr_rf, tpr_rf, _ = roc_curve(y_test, y_probs_rf)
roc_auc_rf = auc(fpr_rf, tpr_rf)

fpr_gb, tpr_gb, _ = roc_curve(y_test, y_probs_gb)
roc_auc_gb = auc(fpr_gb, tpr_gb)

fpr_lg, tpr_lg, _ = roc_curve(y_test, y_probs_lg)
roc_auc_lg = auc(fpr_lg, tpr_lg)

# Plotten
fig_roc = go.Figure()
fig_roc.add_trace(go.Scatter(x=fpr_rf, y=tpr_rf, name=f'Random Forest (AUC = {roc_auc_rf:.3f})'))
fig_roc.add_trace(go.Scatter(x=fpr_gb, y=tpr_gb, name=f'Gradient Boosting (AUC = {roc_auc_gb:.3f})'))
fig_roc.add_trace(go.Scatter(x=fpr_lg, y=tpr_lg, name=f'Logistische Regression (AUC = {roc_auc_lg:.3f})'))


# Diagonale (Zufallslinie)
fig_roc.add_trace(go.Scatter(x=[0, 1], y=[0, 1], mode='lines', line=dict(dash='dash'), name='Zufall'))

fig_roc.update_layout(title='ROC Kurve Vergleich', xaxis_title='False Positive Rate', yaxis_title='True Positive Rate')
fig_roc.show()